# Installing CARTOframes and Setup

In [1]:
# in this notebook, we will use cartoframes 1.0 beta 7:
!pip install cartoframes==1.0b7

# loading some other general notebook libraries 
from IPython.display import clear_output, IFrame 
from IPython.core.display import display, HTML

#just to clean up our output, we will use clear_output()
clear_output()

print("CARTOframes installed to the runtime")

CARTOframes installed to the runtime


In [0]:
from cartoframes.auth import set_default_credentials

user0 = 'athomsoncdb' # enter your CARTO username
key0 = '27294497766d62b0a42d2a151e18a963ea7bdddb' # enter your master API key

set_default_credentials(
    username=user0,
    api_key=key0
)

In [0]:
# importing other modules
import pandas as pd
import geopandas as gpd
import numpy as np

# setting up dataframe display options
pd.options.display.max_columns = None
pd.options.display.max_rows = None
pd.reset_option('max_colwidth')

# Step 1: Data
This is _your_ business data, that we will connect to and analytically prepare with CARTO!

## Loading stations and trips data from Indego

The files are from https://www.rideindego.com/about/data/, though this page seems to be configured to prevent downloads from Python and other "scrapers" - good feedback for you to consider! So we've pre-downloaded the CSVs and hosted them on Github. The following _workflow_ is similar to if we used the data direct from your site though!

In [4]:
''' The Indego URL prevents access via Python.
So we just dragged+dropped to CARTO first and will pretend we downloaded as CSV from your site once you've updated!
url = 'http://u626n26h74f16ig1p3pt0f2g-wpengine.netdna-ssl.com/wp-content/uploads/2019/10/indego-trips-2019-q3-1.zip'
'''

remote_trips_data = 'https://github.com/andrewbt/indego-data/raw/master/indego-trips-2019-q3-1.zip'
df_trips = pd.read_csv(remote_trips_data)
df_trips.head(2)

trip_id  duration     start_time       end_time  start_station  \
0  320093117        30  7/1/2019 0:01  7/1/2019 0:31           3049   
1  320093114        26  7/1/2019 0:04  7/1/2019 0:30           3119   

   start_lat  start_lon  end_station   end_lat    end_lon  bike_id  \
0  39.945091 -75.142502         3121  39.97414 -75.180222    11901   
1  39.966740 -75.207993         3118  39.95866 -75.213226    16519   

   plan_duration trip_route_category passholder_type bike_type  
0             30             One Way        Indego30  standard  
1             30             One Way        Indego30  electric

In [5]:
remote_stations_data = 'https://github.com/andrewbt/indego-data/raw/master/indego-stations-2019-10-1.csv'

df_stations = pd.read_csv(remote_stations_data)
df_stations.head(2)

Station_ID                       Station_Name Day of Go_live_date  Status
0        3000                    Virtual Station           4/23/2015  Active
1        3004  Municipal Services Building Plaza           4/23/2015  Active

## Upload data to CARTO and prepare with PostGIS/SQL
The CSVs/DataFrames by themselves aren't properly geocoded for mapping yet, so in addition to uploading them to our CARTO account, we'll geocode and process them with CARTO's built-in PostGIS database functions so it will be easier for colleagues to use the data in Builder later.

### Trip Start points

#### Create CartoDataFrame

In [9]:
from cartoframes import CartoDataFrame

# Clean latitude and longitude values that are NaN
df_trips = df_trips[df_trips.start_lon == df_trips.start_lon]
df_trips = df_trips[df_trips.start_lat == df_trips.start_lat]

cdf_trip_starts = CartoDataFrame(df_trips)

# Set a geometry column from the coordinates
cdf_trip_starts.set_geometry_from_xy('start_lon', 'start_lat', inplace=True)

cdf_trip_starts.head()

trip_id  duration     start_time       end_time  start_station  \
0  320093117        30  7/1/2019 0:01  7/1/2019 0:31           3049   
1  320093114        26  7/1/2019 0:04  7/1/2019 0:30           3119   
2  320093115        10  7/1/2019 0:04  7/1/2019 0:14           3043   
3  320093116        10  7/1/2019 0:04  7/1/2019 0:14           3043   
4  320093113        15  7/1/2019 0:05  7/1/2019 0:20           3040   

   start_lat  start_lon  end_station    end_lat    end_lon  bike_id  \
0  39.945091 -75.142502         3121  39.974140 -75.180222    11901   
1  39.966740 -75.207993         3118  39.958660 -75.213226    16519   
2  39.930820 -75.174744         3155  39.940182 -75.154419     2729   
3  39.930820 -75.174744         3155  39.940182 -75.154419     2603   
4  39.962891 -75.166061         3007  39.945171 -75.159927    11868   

   plan_duration trip_route_category passholder_type bike_type  \
0             30             One Way        Indego30  standard   
1             30             One Way        Indego30  electric   
2            365             One Way       Indego365  standard   
3             30             One Way        Indego30  standard   
4              1             One Way        Day Pass  standard   

                     geometry  
0  POINT (-75.14250 39.94509)  
1  POINT (-75.20799 39.96674)  
2  POINT (-75.17474 39.93082)  
3  POINT (-75.17474 39.93082)  
4  POINT (-75.16606 39.96289)

In [10]:
cdf_trip_starts.viz()

#### Then upload trip starts to CARTO

In [11]:
cdf_trip_starts.to_carto('indego_trip_starts', if_exists='replace')

Success! Data uploaded correctly


### Trip End points

In [14]:
from cartoframes import CartoDataFrame

# Clean latitude and longitude values that are NaN
df_trips = df_trips[df_trips.end_lon == df_trips.end_lon]
df_trips = df_trips[df_trips.end_lat == df_trips.end_lat]

cdf_trip_ends = CartoDataFrame(df_trips)

# Set a geometry column from the coordinates
cdf_trip_ends.set_geometry_from_xy('end_lon', 'end_lat', inplace=True)

cdf_trip_ends.head()

trip_id  duration     start_time       end_time  start_station  \
0  320093117        30  7/1/2019 0:01  7/1/2019 0:31           3049   
1  320093114        26  7/1/2019 0:04  7/1/2019 0:30           3119   
2  320093115        10  7/1/2019 0:04  7/1/2019 0:14           3043   
3  320093116        10  7/1/2019 0:04  7/1/2019 0:14           3043   
4  320093113        15  7/1/2019 0:05  7/1/2019 0:20           3040   

   start_lat  start_lon  end_station    end_lat    end_lon  bike_id  \
0  39.945091 -75.142502         3121  39.974140 -75.180222    11901   
1  39.966740 -75.207993         3118  39.958660 -75.213226    16519   
2  39.930820 -75.174744         3155  39.940182 -75.154419     2729   
3  39.930820 -75.174744         3155  39.940182 -75.154419     2603   
4  39.962891 -75.166061         3007  39.945171 -75.159927    11868   

   plan_duration trip_route_category passholder_type bike_type  \
0             30             One Way        Indego30  standard   
1             30             One Way        Indego30  electric   
2            365             One Way       Indego365  standard   
3             30             One Way        Indego30  standard   
4              1             One Way        Day Pass  standard   

                     geometry  
0  POINT (-75.18022 39.97414)  
1  POINT (-75.21323 39.95866)  
2  POINT (-75.15442 39.94018)  
3  POINT (-75.15442 39.94018)  
4  POINT (-75.15993 39.94517)

In [15]:
cdf_trip_ends.viz()

#### Upload trip ends to CARTO

In [16]:
cdf_trip_ends.to_carto('indego_trip_ends', if_exists='replace')

Success! Data uploaded correctly


### Indego Stations

This one doesn't have any geometry info, so we'll upload first and then use SQL to join on station ID with the lat/longs from the trips file.

In [17]:
from cartoframes import CartoDataFrame

cdf_stations = CartoDataFrame(df_stations)

cdf_stations.to_carto('indego_stations', if_exists='replace')

Success! Data uploaded correctly


In [18]:
from cartoframes.data.clients import SQLClient

sql = SQLClient()

#The CartoDBfy function will add CARTO's required geometry columns
sql.query("SELECT cdb_cartodbfytable('athomsoncdb', 'indego_stations');")

[{'cdb_cartodbfytable': 'indego_stations'}]

In [19]:
sql.schema('indego_stations')

Column name          Column type     
-------------------------------------
cartodb_id           number          
the_geom             geometry        
the_geom_webmercator geometry        
station_id           number          
station_name         string          
day_of_go_live_date  string          
status               string          


In [20]:
job = sql.execute('UPDATE indego_stations AS s SET the_geom = t.the_geom FROM indego_trip_starts AS t WHERE s.station_id = t.start_station')

print('check status with: https://' + user0 + '.carto.com/api/v2/sql/job/' + job['job_id'] + '?api_key=' + key0)

check status with: https://athomsoncdb.carto.com/api/v2/sql/job/7803899a-b46d-4d3f-8e56-7e9a0618ea48?api_key=27294497766d62b0a42d2a151e18a963ea7bdddb


In [21]:
from cartoframes.viz import Layer

#check to see it was geocoded correctly!
Layer('indego_stations')

In [22]:
#Let's confirm it's cartodbfy'ed and visible in Builder
sql.query("SELECT cdb_cartodbfytable('athomsoncdb', 'indego_stations');")

[{'cdb_cartodbfytable': 'indego_stations'}]

### Create Trip O-D Lines with SQL
We'll use PostGIS' ST_MakeLine() function to join the start points with the ending points

In [24]:
from cartoframes.io.carto import create_table_from_query

od_query = """SELECT ST_MakeLine(CDB_LatLng(start_lat, start_lon), CDB_LatLng(end_lat, end_lon)) as the_geom, 
              trip_id, duration, start_time, end_time, start_station, start_lat, start_lon, end_station, end_lat, end_lon, 
              bike_id, plan_duration, trip_route_category, passholder_type, bike_type FROM indego_trip_ends"""

create_table_from_query(od_query, 'indego_trip_od_lines', if_exists='replace')

Success! Table created correctly


In [25]:
Layer('indego_trip_od_lines')

# Step 2: Data Enrichment Using CARTO's Data Observatory
Our data is now in CARTO and has been fully processed into separate start, end, and trip line tables!

The next step of of the Location Intelligence journey is to obtain other contextual data such as Census demographics and boundaries, which will be valuable for the report on equity metrics to City Council, and other maps in Builder our colleagues make.

Ultimately, we want a background layer of Census Tracts with demographic variables to compare against the bike trips and stations. We can accomplish this with CARTO's Data Observatory, purpose-built for quickly obtaining enrichment data for your analyses.

## Obtaining Boundaries

### Philadelphia County

A larger area is useful for later querying smaller boundaries that lay within it, like census tracts.

In [26]:
from cartoframes.data.clients import DataObsClient
from cartoframes.viz import Map, Layer

do = DataObsClient()

phila_county = do.boundaries(
    boundary='us.census.tiger.county',
    region='indego_trip_starts', decode_geom=True)
Map(Layer(phila_county))

In [27]:
# Upload as a CARTO table
from cartoframes.io.carto import to_carto
to_carto(phila_county, 'philadelphia_county',if_exists='replace')

Success! Data uploaded correctly


### Census Tracts

We'll use the county boundary later to query CARTO's DO for all Census Tracts which lay within the county.

CARTO has also already done the work of creating cartography-friendly shoreline-clipped Census boundaries.

In [28]:
phila_tracts = do.boundaries(
    boundary='us.census.tiger.census_tract_clipped',
    region='philadelphia_county', decode_geom=True)
Layer(phila_tracts)

In [29]:
# Upload tracts as a CARTO table
to_carto(phila_tracts, 'philadelphia_tracts',if_exists='replace')

Success! Data uploaded correctly


## Enriching the tract boundaries with Demographic Variables

CARTO's Data Observatory includes not only boundary data, but variables/measures as well, straight from the Census' American Community Survey. We'll select four relevant examples:
- Median Income
- Commuting
- Total Population
- Education

### Median Income

In [30]:
# gather metadata needed to look up median income
median_income_meta = do.discovery(
    'philadelphia_tracts',
    keywords='median income',
    time='2011 - 2015',
    boundaries='us.census.tiger.census_tract_clipped')
median_income_meta

denom_aggregate denom_colname  \
0             sum    households   
1             sum    households   

                                   denom_description denom_geomref_colname  \
0  A count of the number of households in each ge...               geoidsc   
1  A count of the number of households in each ge...               geoidsc   

                  denom_id  denom_name denom_reltype denom_t_description  \
0  us.census.acs.B11001001  Households      universe                None   
1  us.census.acs.B11001001  Households      universe                None   

                                denom_tablename denom_type geom_colname  \
0  obs_9effa577f8b5d674d620dfbaf4aec55e70ac06b8    Numeric     the_geom   
1  obs_9effa577f8b5d674d620dfbaf4aec55e70ac06b8    Numeric     the_geom   

                                  geom_description geom_geomref_colname  \
0  A cartography-ready version of US Census Tracts                geoid   
1  A cartography-ready version of US Census Tracts                geoid   

                                geom_id                           geom_name  \
0  us.census.tiger.census_tract_clipped  Shoreline clipped US Census Tracts   
1  us.census.tiger.census_tract_clipped  Shoreline clipped US Census Tracts   

  geom_t_description                                geom_tablename  \
0               None  obs_a852194c8e1fb99ec02b857e9d697f6a4ebb8153   
1               None  obs_a852194c8e1fb99ec02b857e9d697f6a4ebb8153   

  geom_timespan geom_type   id max_score_rank max_timespan_rank  \
0          2015  Geometry  1.0           None              None   
1          2015  Geometry  2.0           None              None   

    normalization   num_geoms numer_aggregate  numer_colname  \
0  predenominated  203.743081          median  median_income   
1   prenormalized  203.743081          median  median_income   

                                   numer_description numer_geomref_colname  \
0  Within a geographic area, the median income re...               geoidsc   
1  Within a geographic area, the median income re...               geoidsc   

                  numer_id                                     numer_name  \
0  us.census.acs.B19013001  Median Household Income in the past 12 Months   
1  us.census.acs.B19013001  Median Household Income in the past 12 Months   

  numer_t_description                               numer_tablename  \
0                None  obs_9effa577f8b5d674d620dfbaf4aec55e70ac06b8   
1                None  obs_9effa577f8b5d674d620dfbaf4aec55e70ac06b8   

  numer_timespan numer_type      score  score_rank  score_rownum  \
0    2011 - 2015    Numeric  75.022187         1.0           1.0   
1    2011 - 2015    Numeric  75.022187         1.0           1.0   

            suggested_name target_area target_geoms  timespan_rank  \
0  median_income_2011_2015        None         None            1.0   
1  median_income_2011_2015        None         None            1.0   

   timespan_rownum  
0              1.0  
1              1.0

In [0]:
median_income_aug_df = median_income_meta.iloc[[0]] #get just the one measure we need

### Commute

In [32]:
# gather metadata needed to look up commute measures
commute_meta = do.discovery(
    'philadelphia_tracts',
    keywords='commute',
    time='2011 - 2015',
    boundaries='us.census.tiger.census_tract_clipped')
commute_meta

denom_aggregate                       denom_colname  \
0              sum                 workers_16_and_over   
1              sum                 workers_16_and_over   
2              sum          commuters_by_car_truck_van   
3              sum          commuters_by_car_truck_van   
4              sum          commuters_by_car_truck_van   
5              sum          commuters_by_car_truck_van   
6              sum  commuters_by_public_transportation   
7              sum  commuters_by_public_transportation   
8              sum  commuters_by_public_transportation   
9              sum  commuters_by_public_transportation   
10             sum                   commuters_16_over   
11             sum                   commuters_16_over   
12             sum                   commuters_16_over   
13             sum                   commuters_16_over   
14             sum                   commuters_16_over   
15             sum                   commuters_16_over   
16             sum                 workers_16_and_over   
17             sum                 workers_16_and_over   
18             sum                   commuters_16_over   
19             sum                   commuters_16_over   
20             sum                   commuters_16_over   
21             sum                   commuters_16_over   
22             sum                   commuters_16_over   
23             sum                   commuters_16_over   
24             sum                   commuters_16_over   
25             sum                   commuters_16_over   
26             sum                   commuters_16_over   
27             sum                   commuters_16_over   
28             sum                   commuters_16_over   
29             sum                   commuters_16_over   
30             sum                   commuters_16_over   
31             sum                   commuters_16_over   
32             sum                   commuters_16_over   
33             sum                   commuters_16_over   
34             sum                   commuters_16_over   
35             sum                   commuters_16_over   
36             sum                   commuters_16_over   
37             sum                   commuters_16_over   
38             sum                   commuters_16_over   
39             sum                   commuters_16_over   

                                    denom_description denom_geomref_colname  \
0   The number of people in each geography who wor...               geoidsc   
1   The number of people in each geography who wor...               geoidsc   
2   The number of workers age 16 years and over wi...               geoidsc   
3   The number of workers age 16 years and over wi...               geoidsc   
4   The number of workers age 16 years and over wi...               geoidsc   
5   The number of workers age 16 years and over wi...               geoidsc   
6   The number of workers age 16 years and over wi...               geoidsc   
7   The number of workers age 16 years and over wi...               geoidsc   
8   The number of workers age 16 years and over wi...               geoidsc   
9   The number of workers age 16 years and over wi...               geoidsc   
10  The number of workers in a geographic area ove...               geoidsc   
11  The number of workers in a geographic area ove...               geoidsc   
12  The number of workers in a geographic area ove...               geoidsc   
13  The number of workers in a geographic area ove...               geoidsc   
14  The number of workers in a geographic area ove...               geoidsc   
15  The number of workers in a geographic area ove...               geoidsc   
16  The number of people in each geography who wor...               geoidsc   
17  The number of people in each geography who wor...               geoidsc   
18  The number of workers in a geographic area ove...               geoidsc   
19  The number of workers in a geographic ar

In [0]:
commute_aug_df = commute_meta.iloc[[17]] #get just the one commute measure we need

### Total Population

In [34]:
# gather metadata needed to look up population measures
population_meta = do.discovery(
    'philadelphia_tracts',
    keywords='total population',
    time='2011 - 2015',
    boundaries='us.census.tiger.census_tract_clipped')
population_meta

denom_aggregate denom_colname  \
0            None          None   
1            None          None   
2             sum     total_pop   
3             sum     total_pop   

                                   denom_description denom_geomref_colname  \
0                                               None                  None   
1                                               None                  None   
2  The total number of all people living in a giv...               geoidsc   
3  The total number of all people living in a giv...               geoidsc   

                  denom_id        denom_name denom_reltype  \
0                     None              None          None   
1                     None              None          None   
2  us.census.acs.B01003001  Total Population      universe   
3  us.census.acs.B01003001  Total Population      universe   

  denom_t_description                               denom_tablename  \
0                None                                          None   
1                None                                          None   
2                None  obs_9effa577f8b5d674d620dfbaf4aec55e70ac06b8   
3                None  obs_9effa577f8b5d674d620dfbaf4aec55e70ac06b8   

  denom_type geom_colname                                 geom_description  \
0       None     the_geom  A cartography-ready version of US Census Tracts   
1       None     the_geom  A cartography-ready version of US Census Tracts   
2    Numeric     the_geom  A cartography-ready version of US Census Tracts   
3    Numeric     the_geom  A cartography-ready version of US Census Tracts   

  geom_geomref_colname                               geom_id  \
0                geoid  us.census.tiger.census_tract_clipped   
1                geoid  us.census.tiger.census_tract_clipped   
2                geoid  us.census.tiger.census_tract_clipped   
3                geoid  us.census.tiger.census_tract_clipped   

                            geom_name geom_t_description  \
0  Shoreline clipped US Census Tracts               None   
1  Shoreline clipped US Census Tracts               None   
2  Shoreline clipped US Census Tracts               None   
3  Shoreline clipped US Census Tracts               None   

                                 geom_tablename geom_timespan geom_type   id  \
0  obs_a852194c8e1fb99ec02b857e9d697f6a4ebb8153          2015  Geometry  1.0   
1  obs_a852194c8e1fb99ec02b857e9d697f6a4ebb8153          2015  Geometry  2.0   
2  obs_a852194c8e1fb99ec02b857e9d697f6a4ebb8153          2015  Geometry  5.0   
3  obs_a852194c8e1fb99ec02b857e9d697f6a4ebb8153          2015  Geometry  6.0   

  max_score_rank max_timespan_rank   normalization   num_geoms  \
0           None              None  predenominated  203.743081   
1           None              None            area  203.743081   
2           None              None  predenominated  203.743081   
3           None              None   prenormalized  203.743081   

  numer_aggregate      numer_colname  \
0             sum          total_pop   
1             sum          total_pop   
2         average  income_per_capita   
3         average  income_per_capita   

                                   numer_description numer_geomref_colname  \
0  The total number of all people living in a giv...               geoidsc   
1  The total number of all people living in a giv...               geoidsc   
2  Per capita income is the mean income computed ...               geoidsc   
3  Per capita income is the mean income computed ...               geoidsc   

                  numer_id                               numer_name  \
0  us.census.acs.B01003001                         Total Population   
1  us.census.acs.B01003001                         Total Population   
2  us.census.acs.B19301001  Per Capita Income in the past 12 Months   
3  us.census.acs.B19301001  Per Capita Income in the past 12 Months   

  numer_t_description                               numer_tablename  \
0   

In [0]:
pop_aug_df = population_meta.iloc[[0]] #get just the one population measure we need

### Education

In [36]:
# gather metadata needed to look up education measures
education_meta = do.discovery(
    'philadelphia_tracts',
    keywords='high school',
    time='2011 - 2015',
    boundaries='us.census.tiger.census_tract_clipped')
education_meta

denom_aggregate      denom_colname  \
0             sum  pop_25_years_over   
1             sum  pop_25_years_over   
2             sum  pop_25_years_over   
3             sum  pop_25_years_over   
4             sum          in_school   
5             sum          in_school   
6             sum  pop_25_years_over   
7             sum  pop_25_years_over   

                                   denom_description denom_geomref_colname  \
0  The number of people in a geographic area who ...               geoidsc   
1  The number of people in a geographic area who ...               geoidsc   
2  The number of people in a geographic area who ...               geoidsc   
3  The number of people in a geographic area who ...               geoidsc   
4  The total number of people in each geography c...               geoidsc   
5  The total number of people in each geography c...               geoidsc   
6  The number of people in a geographic area who ...               geoidsc   
7  The number of people in a geographic area who ...               geoidsc   

                  denom_id                    denom_name denom_reltype  \
0  us.census.acs.B15003001  Population 25 Years and Over   denominator   
1  us.census.acs.B15003001  Population 25 Years and Over   denominator   
2  us.census.acs.B15003001  Population 25 Years and Over   denominator   
3  us.census.acs.B15003001  Population 25 Years and Over   denominator   
4  us.census.acs.B14001002   Students Enrolled in School   denominator   
5  us.census.acs.B14001002   Students Enrolled in School   denominator   
6  us.census.acs.B15003001  Population 25 Years and Over   denominator   
7  us.census.acs.B15003001  Population 25 Years and Over   denominator   

  denom_t_description                               denom_tablename  \
0                None  obs_9effa577f8b5d674d620dfbaf4aec55e70ac06b8   
1                None  obs_9effa577f8b5d674d620dfbaf4aec55e70ac06b8   
2                None  obs_9effa577f8b5d674d620dfbaf4aec55e70ac06b8   
3                None  obs_9effa577f8b5d674d620dfbaf4aec55e70ac06b8   
4                None  obs_9effa577f8b5d674d620dfbaf4aec55e70ac06b8   
5                None  obs_9effa577f8b5d674d620dfbaf4aec55e70ac06b8   
6                None  obs_9effa577f8b5d674d620dfbaf4aec55e70ac06b8   
7                None  obs_9effa577f8b5d674d620dfbaf4aec55e70ac06b8   

  denom_type geom_colname                                 geom_description  \
0    Numeric     the_geom  A cartography-ready version of US Census Tracts   
1    Numeric     the_geom  A cartography-ready version of US Census Tracts   
2    Numeric     the_geom  A cartography-ready version of US Census Tracts   
3    Numeric     the_geom  A cartography-ready version of US Census Tracts   
4    Numeric     the_geom  A cartography-ready version of US Census Tracts   
5    Numeric     the_geom  A cartography-ready version of US Census Tracts   
6    Numeric     the_geom  A cartography-ready version of US Census Tracts   
7    Numeric     the_geom  A cartography-ready version of US Census Tracts   

  geom_geomref_colname                               geom_id  \
0                geoid  us.census.tiger.census_tract_clipped   
1                geoid  us.census.tiger.census_tract_clipped   
2                geoid  us.census.tiger.census_tract_clipped   
3                geoid  us.census.tiger.census_tract_clipped   
4                geoid  us.census.tiger.census_tract_clipped   
5                geoid  us.census.tiger.census_tract_clipped   
6                geoid  us.census.tiger.census_tract_clipped   
7                geoid  us.census.tiger.census_tract_clipped   

                            geom_name geom_t_description  \
0  Shoreline clipped US Census Tracts               None   
1  Shoreline clipped US Census Tracts               None   
2  Shoreline clipped US Census Tracts               None   
3  Shoreline clipped US Census Tracts               None   
4  Shoreline clipped US Census Tracts              

In [0]:
edu_aug_df = education_meta.iloc[[1]] #get just the one education measure we need

### Collect all measures and enrich the CARTO table

In [38]:
df_all_meta = pd.concat([median_income_aug_df, commute_aug_df, pop_aug_df, edu_aug_df], ignore_index=True)
df_all_meta

denom_aggregate        denom_colname  \
0             sum           households   
1             sum  workers_16_and_over   
2            None                 None   
3             sum    pop_25_years_over   

                                   denom_description denom_geomref_colname  \
0  A count of the number of households in each ge...               geoidsc   
1  The number of people in each geography who wor...               geoidsc   
2                                               None                  None   
3  The number of people in a geographic area who ...               geoidsc   

                  denom_id                    denom_name denom_reltype  \
0  us.census.acs.B11001001                    Households      universe   
1  us.census.acs.B08006001    Workers over the Age of 16   denominator   
2                     None                          None          None   
3  us.census.acs.B15003001  Population 25 Years and Over   denominator   

  denom_t_description                               denom_tablename  \
0                None  obs_9effa577f8b5d674d620dfbaf4aec55e70ac06b8   
1                None  obs_9effa577f8b5d674d620dfbaf4aec55e70ac06b8   
2                None                                          None   
3                None  obs_9effa577f8b5d674d620dfbaf4aec55e70ac06b8   

  denom_type geom_colname                                 geom_description  \
0    Numeric     the_geom  A cartography-ready version of US Census Tracts   
1    Numeric     the_geom  A cartography-ready version of US Census Tracts   
2       None     the_geom  A cartography-ready version of US Census Tracts   
3    Numeric     the_geom  A cartography-ready version of US Census Tracts   

  geom_geomref_colname                               geom_id  \
0                geoid  us.census.tiger.census_tract_clipped   
1                geoid  us.census.tiger.census_tract_clipped   
2                geoid  us.census.tiger.census_tract_clipped   
3                geoid  us.census.tiger.census_tract_clipped   

                            geom_name geom_t_description  \
0  Shoreline clipped US Census Tracts               None   
1  Shoreline clipped US Census Tracts               None   
2  Shoreline clipped US Census Tracts               None   
3  Shoreline clipped US Census Tracts               None   

                                 geom_tablename geom_timespan geom_type    id  \
0  obs_a852194c8e1fb99ec02b857e9d697f6a4ebb8153          2015  Geometry   1.0   
1  obs_a852194c8e1fb99ec02b857e9d697f6a4ebb8153          2015  Geometry  34.0   
2  obs_a852194c8e1fb99ec02b857e9d697f6a4ebb8153          2015  Geometry   1.0   
3  obs_a852194c8e1fb99ec02b857e9d697f6a4ebb8153          2015  Geometry   2.0   

  max_score_rank max_timespan_rank   normalization   num_geoms  \
0           None              None  predenominated  203.743081   
1           None              None     denominated  203.743081   
2           None              None  predenominated  203.743081   
3           None              None     denominated  203.743081   

  numer_aggregate                       numer_colname  \
0          median                       median_income   
1             sum  commuters_by_public_transportation   
2             sum                           total_pop   
3             sum      less_than_high_school_graduate   

                                   numer_description numer_geomref_colname  \
0  Within a geographic area, the median income re...               geoidsc   
1  The number of workers age 16 years and over wi...               geoidsc   
2  The total number of all people living in a giv...               geoidsc   
3  The number of people in a geographic area over...               geoidsc   

                  numer_id                                     numer_name  \
0  us.census.acs.B19013001  Median Household Income in the past 12 Months   
1  us.census.acs.B08301010             Commuters by Public Transportation   
2  us.census.ac

In [39]:
philadelphia_all_measures = do.augment(
    'philadelphia_tracts',
    df_all_meta,
    how='geom_refs')
philadelphia_all_measures.head(2)

geom_refs                                           the_geom  cartodb_id  \
0  42017100103  0103000020E61000000100000057000000D85DA0A4C0BD...           1   
1  42017100104  0103000020E61000000100000075000000FE756EDA8CBD...           2   

   median_income_2011_2015  \
0                  42632.0   
1                  35930.0   

   commuters_by_public_transportation_2011_2015_by_workers_16_and_  \
0                                           0.043053                 
1                                           0.050145                 

   total_pop_2011_2015  \
0               2456.0   
1               4347.0   

   less_than_high_school_graduate_2011_2015_by_pop_25_years_over  
0                                           0.102041              
1                                           0.117046

In [42]:
to_carto(philadelphia_all_measures, 'philadelphia_tracts_enriched', if_exists='replace', force_cartodbfy=True)

Success! Data uploaded correctly


In [43]:
from cartoframes.viz.helpers import color_continuous_layer
Map(color_continuous_layer('philadelphia_tracts_enriched', 'total_pop_2011_2015'))

The final dataset will be available in Builder for our colleagues to build their own maps with.